# Supervised Learning


In [ ]:
from google.colab import drive

import pandas as pd
import numpy as np

from sklearn.tree import DecisionTreeClassifier, ExtraTreeClassifier
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier, GradientBoostingClassifier, AdaBoostClassifier, HistGradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_validate
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from xgboost import XGBClassifier

from sklearn.feature_selection import SelectKBest, chi2

from tqdm import tqdm
import joblib

from IPython.display import Image, Audio, display
from ipywidgets import widgets

# Data Preparation

In [ ]:
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!cp "/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/database.csv" .
!cp "/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/classificacao_anomalias.csv" .

In [ ]:
data = pd.read_csv('/content/database.csv')
tutor = pd.read_csv('/content/classificacao_anomalias.csv')

In [ ]:
tutor = tutor[['File Name','Label']]
tutor['Label'] = tutor['Label'].apply(lambda x: 1 if x == 0 else 0)

tutor.rename(columns={'File Name':'file'}, inplace=True)
tutor.set_index('file',inplace=True)

data['file'] = data['file'].apply(lambda x: x.split('/')[-1])
data.set_index('file', inplace=True)

<ipython-input-20-a2be10720b21>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tutor['Label'] = tutor['Label'].apply(lambda x: 1 if x == 0 else 0)
<ipython-input-20-a2be10720b21>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tutor.rename(columns={'File Name':'file'}, inplace=True)


In [ ]:
tutor.head(3)

Label
file             
a00001.mp3      1
a00002.mp3      0
a00003.mp3      1

In [ ]:
data.head(3)

spectral_centroids_mean_0  spectral_centroids_std_0  \
file                                                              
a00299.mp3                1731.058284                 335.62239   
a00299.mp3                2558.297363                 463.08374   
a00299.mp3                1731.036693                 335.02160   

            spectral_centroids_ptp_0  spectral_contrast_mean_0  \
file                                                             
a00299.mp3               1898.014062                 22.745991   
a00299.mp3               2773.123755                 21.869725   
a00299.mp3               1874.092648                 22.723278   

            spectral_contrast_std_0  spectral_contrast_ptp_0  \
file                                                           
a00299.mp3                 4.557550                40.922714   
a00299.mp3                 4.523453                40.755000   
a00299.mp3                 4.656667                37.843531   

            spectral_contrast_mean_1  spectral_contrast_std_1  \
file                                                            
a00299.mp3                 10.487578                 3.227850   
a00299.mp3                 10.416972                 3.099111   
a00299.mp3                 10.319537                 3.115737   

            spectral_contrast_ptp_1  spectral_contrast_mean_2  ...  \
file                                                           ...   
a00299.mp3                27.333287                 12.420757  ...   
a00299.mp3                26.726065                 12.460622  ...   
a00299.mp3                20.041797                 12.466053  ...   

            melspectrogram_mean_125  melspectrogram_std_125  \
file                                                          
a00299.mp3                 0.000090                0.000032   
a00299.mp3                 0.000369                0.000086   
a00299.mp3                 0.000090                0.000032   

            melspectrogram_ptp_125  melspectrogram_mean_126  \
file                                                          
a00299.mp3                0.000203                 0.000042   
a00299.mp3                0.000531                 0.000330   
a00299.mp3                0.000185                 0.000042   

            melspectrogram_std_126  melspectrogram_ptp_126  \
file                                                         
a00299.mp3                0.000016                0.000102   
a00299.mp3                0.000075                0.000506   
a00299.mp3                0.000016                0.000105   

            melspectrogram_mean_127  melspectrogram_std_127  \
file                                                          
a00299.mp3                 0.000004                0.000002   
a00299.mp3                 0.000289                0.000065   
a00299.mp3                 0.000004                0.000002   

            melspectrogram_ptp_127  duration  
file                                          
a00299.mp3                0.000010  14.88254  
a00299.mp3                0.000381  14.88254  
a00299.mp3                0.000011  14.88254  

[3 rows x 535 columns]

In [ ]:
data_labeled = data.join(tutor, how='inner')
data_labeled.dropna(inplace=True, axis=0)
print(data_labeled.shape)
data_labeled.head(10)

(1960, 536)


spectral_centroids_mean_0  spectral_centroids_std_0  \
file                                                              
a00001.mp3                1502.320863                588.027103   
a00001.mp3                2763.122652               1192.364685   
a00001.mp3                1491.082546                534.348181   
a00001.mp3                1502.560435                588.253305   
a00002.mp3                1840.960213               1214.529160   
a00002.mp3                2803.200031               1590.989856   
a00002.mp3                1839.387081               1210.202554   
a00002.mp3                1841.727599               1214.742523   
a00003.mp3                1870.773330                678.721149   
a00003.mp3                3200.340643               1216.209382   

            spectral_centroids_ptp_0  spectral_contrast_mean_0  \
file                                                             
a00001.mp3               4880.781588                 24.550558   
a00001.mp3               4902.298091                 19.106679   
a00001.mp3               2791.792247                 24.233943   
a00001.mp3               4888.163598                 24.495059   
a00002.mp3               4392.220910                 20.023244   
a00002.mp3               5120.703647                 18.843350   
a00002.mp3               4387.678485                 20.185468   
a00002.mp3               4392.909731                 20.215824   
a00003.mp3               4878.096306                 23.674225   
a00003.mp3               4766.839883                 17.174075   

            spectral_contrast_std_0  spectral_contrast_ptp_0  \
file                                                           
a00001.mp3                 5.907505                42.986954   
a00001.mp3                 5.406112                29.747178   
a00001.mp3                 6.082253                46.864972   
a00001.mp3                 5.548426                37.872689   
a00002.mp3                 5.948771                40.483916   
a00002.mp3                 6.501181                37.876636   
a00002.mp3                 6.196013                41.915061   
a00002.mp3                 5.929752                42.481673   
a00003.mp3                 5.037725                32.809746   
a00003.mp3                 5.132355                29.110568   

            spectral_contrast_mean_1  spectral_contrast_std_1  \
file                                                            
a00001.mp3                 10.593247                 3.371684   
a00001.mp3                 10.707292                 3.294758   
a00001.mp3                 10.395710                 2.888752   
a00001.mp3                 10.580460                 3.409529   
a00002.mp3                 11.379677                 4.307745   
a00002.mp3                 11.184041                 4.210148   
a00002.mp3                 11.313299                 4.279571   
a00002.mp3                 11.122532                 4.366323   
a00003.mp3                 10.439965                 3.013229   
a00003.mp3                 10.620644                 3.181570   

            spectral_contrast_ptp_1  spectral_contrast_mean_2  ...  \
file                                                           ...   
a00001.mp3                20.125378                 12.880371  ...   
a00001.mp3                18.710304                 12.970098  ...   
a00001.mp3                16.388397                 12.631969  ...   
a00001.mp3                22.795916                 12.808089  ...   
a00002.mp3                27.995051                 13.885996  ...   
a00002.mp3                26.785361                 13.532515  ...   
a00002.mp3                22.896118                 13.860248  ...   
a00002.mp3                25.654639                 13.691293  ...   
a00003.mp3                16.695223                 12.658699  ...   
a00003.mp3                19.372686                 12.678881  ...   

            melspectrog

In [ ]:
data_labeled

file  spectral_centroids_mean_0  spectral_centroids_std_0  \
0     a00001.mp3                1502.320863                588.027103   
1     a00001.mp3                2763.122652               1192.364685   
2     a00001.mp3                1491.082546                534.348181   
3     a00001.mp3                1502.560435                588.253305   
4     a00002.mp3                1840.960213               1214.529160   
...          ...                        ...                       ...   
1955  a00517.mp3                1435.037576                165.835812   
1956  a00518.mp3                1436.571378                579.632383   
1957  a00518.mp3                1759.498864                962.175950   
1958  a00518.mp3                1436.978718                579.696862   
1959  a00518.mp3                1436.573180                579.630456   

      spectral_centroids_ptp_0  spectral_contrast_mean_0  \
0                  4880.781588                 24.550558   
1                  4902.298091                 19.106679   
2                  2791.792247                 24.233943   
3                  4888.163598                 24.495059   
4                  4392.220910                 20.023244   
...                        ...                       ...   
1955               1204.793793                 21.098754   
1956               2627.151817                 17.230332   
1957               3609.867952                 17.170958   
1958               2652.638356                 17.169668   
1959               2627.160404                 17.241958   

      spectral_contrast_std_0  spectral_contrast_ptp_0  \
0                    5.907505                42.986954   
1                    5.406112                29.747178   
2                    6.082253                46.864972   
3                    5.548426                37.872689   
4                    5.948771                40.483916   
...                       ...                      ...   
1955                 4.128975                43.405595   
1956                 5.435188                39.068221   
1957                 5.411570                46.078684   
1958                 5.277206                34.084141   
1959                 5.478876                39.098575   

      spectral_contrast_mean_1  spectral_contrast_std_1  \
0                    10.593247                 3.371684   
1                    10.707292                 3.294758   
2                    10.395710                 2.888752   
3                    10.580460                 3.409529   
4                    11.379677                 4.307745   
...                        ...                      ...   
1955                 11.099777                 3.082866   
1956                 11.151806                 3.611955   
1957                 11.088664                 3.556100   
1958                 11.206248                 3.675907   
1959                 11.151482                 3.611887   

      spectral_contrast_ptp_1  ...  melspectrogram_std_125  \
0                   20.125378  ...                0.000139   
1                   18.710304  ...                0.000158   
2                   16.388397  ...                0.000140   
3                   22.795916  ...                0.000140   
4                   27.995051  ...                0.000140   
...                       ...  ...                     ...   
1955                24.582489  ...                0.000819   
1956                27.821745  ...                0.107613   
1957                29.020094  ...                0.107788   
1958                27.725106  ...                0.107244   
1959                28.360390  ...                0.107613   

      melspectrogram_ptp_125  melspectrogram_mean_126  melspectrogram_std_126  \
0                   0.001725                 0.000034                0.000073   
1                   0.001836                 0.000327                0.000103   
2                   

In [ ]:
data_labeled_norm = data_labeled.copy()
cols_to_normalize = [col for col in data_labeled_norm.columns if col not in ['file', 'duration', 'Label']]
scaler = MinMaxScaler()
data_labeled_norm[cols_to_normalize] = scaler.fit_transform(data_labeled_norm[cols_to_normalize])

X_normalized = data_labeled_norm.drop(columns=['Label'], axis=1)
y = data_labeled_norm['Label']

In [ ]:
X_normalized

spectral_centroids_mean_0  spectral_centroids_std_0  \
file                                                              
a00001.mp3                   0.190247                  0.271587   
a00001.mp3                   0.481223                  0.572089   
a00001.mp3                   0.187653                  0.244896   
a00001.mp3                   0.190302                  0.271700   
a00002.mp3                   0.268400                  0.583110   
...                               ...                       ...   
a00517.mp3                   0.174719                  0.061657   
a00518.mp3                   0.175073                  0.267413   
a00518.mp3                   0.249600                  0.457630   
a00518.mp3                   0.175167                  0.267445   
a00518.mp3                   0.175073                  0.267412   

            spectral_centroids_ptp_0  spectral_contrast_mean_0  \
file                                                             
a00001.mp3                  0.743948                  0.938340   
a00001.mp3                  0.747458                  0.517536   
a00001.mp3                  0.403130                  0.913867   
a00001.mp3                  0.745152                  0.934050   
a00002.mp3                  0.664239                  0.588385   
...                              ...                       ...   
a00517.mp3                  0.144211                  0.671521   
a00518.mp3                  0.376269                  0.372497   
a00518.mp3                  0.536598                  0.367907   
a00518.mp3                  0.380427                  0.367807   
a00518.mp3                  0.376270                  0.373395   

            spectral_contrast_std_0  spectral_contrast_ptp_0  \
file                                                           
a00001.mp3                 0.626029                 0.409862   
a00001.mp3                 0.496602                 0.139940   
a00001.mp3                 0.671138                 0.488924   
a00001.mp3                 0.533338                 0.305597   
a00002.mp3                 0.636681                 0.358832   
...                             ...                      ...   
a00517.mp3                 0.166927                 0.418397   
a00518.mp3                 0.504107                 0.329970   
a00518.mp3                 0.498010                 0.472894   
a00518.mp3                 0.463326                 0.228359   
a00518.mp3                 0.515385                 0.330589   

            spectral_contrast_mean_1  spectral_contrast_std_1  \
file                                                            
a00001.mp3                  0.111170                 0.377133   
a00001.mp3                  0.125645                 0.345474   
a00001.mp3                  0.086098                 0.178386   
a00001.mp3                  0.109547                 0.392707   
a00002.mp3                  0.210986                 0.762359   
...                              ...                      ...   
a00517.mp3                  0.175460                 0.258272   
a00518.mp3                  0.182064                 0.476014   
a00518.mp3                  0.174050                 0.453027   
a00518.mp3                  0.188974                 0.502333   
a00518.mp3                  0.182023                 0.475985   

            spectral_contrast_ptp_1  spectral_contrast_mean_2  ...  \
file                                                           ...   
a00001.mp3                 0.220696                  0.121207  ...   
a00001.mp3                 0.170195                  0.132781  ...   
a00001.mp3                 0.087332                  0.089165  ...   
a00001.mp3                 0.316000                  0.111883  ...   
a00002.mp3                 0.501544                  0.250925  ...   
...                             ...                       ...  ...   
a00517.mp3                 0.379759       

In [ ]:
skb = SelectKBest(chi2, k=50)
X = skb.fit_transform(X_normalized, y)
col_select = skb.get_support(indices=True)
print(X.shape, col_select)

(1960, 50) [ 93 150 152 177 186 189 192 195 198 201 204 205 207 210 213 216 219 222
 225 231 234 237 240 243 246 249 252 253 255 258 261 265 280 312 315 316
 318 319 321 324 325 327 330 333 336 345 346 349 355 380]


In [ ]:
y.shape

(1960,)

# Models

In [ ]:
import warnings
warnings.filterwarnings('ignore')

max_depth = 5

models = [
    DecisionTreeClassifier(random_state=42,max_depth=max_depth),
    ExtraTreeClassifier(random_state=42,max_depth=max_depth),
    RandomForestClassifier(random_state=42,max_depth=max_depth),
    ExtraTreesClassifier(random_state=42,max_depth=max_depth),
    GradientBoostingClassifier(random_state=42,max_depth=max_depth),
    AdaBoostClassifier(random_state=42),
    HistGradientBoostingClassifier(random_state=42,max_depth=max_depth),
    LogisticRegression(random_state=42),
    XGBClassifier(random_state=42),
    SVC()
]

# Evaluate each model using cross-validation
results = []
for model in tqdm(models):
    scores = cross_validate(model, X, y, cv=5, scoring=['f1', 'recall', 'precision'], verbose=1)
    results.append({
        'model': model.__class__.__name__,
        'f1_score': scores['test_f1'].mean(),
        'recall': scores['test_recall'].mean(),
        'precision': scores['test_precision'].mean(),
        'tempo': scores['fit_time'].mean(),
    })

# Create a DataFrame with the results
results_df = pd.DataFrame(results).sort_values(by='f1_score', ascending=False)

results_df

100%|██████████| 10/10 [00:41<00:00,  4.18s/it]


model  f1_score    recall  precision     tempo
3            ExtraTreesClassifier  0.639764  0.717418   0.594688  0.167066
9                             SVC  0.639573  0.777803   0.549031  0.102868
0          DecisionTreeClassifier  0.615019  0.676338   0.573151  0.040849
2          RandomForestClassifier  0.609054  0.666158   0.568258  0.569664
7              LogisticRegression  0.603257  0.715208   0.530751  0.019378
6  HistGradientBoostingClassifier  0.578103  0.600403   0.568442  0.616680
1             ExtraTreeClassifier  0.547788  0.624680   0.519007  0.003388
5              AdaBoostClassifier  0.541335  0.563582   0.532838  0.733185
4      GradientBoostingClassifier  0.537939  0.545698   0.538716  5.494858
8                   XGBClassifier  0.536840  0.563501   0.525406  0.451721

In [ ]:
# Save the model with the best f1_score
best_model = results_df.iloc[0]['model']

print(best_model)

best_model_object = next(model for model in models if model.__class__.__name__ == best_model)

# Fit the best model with the data
best_model_object.fit(X, y)

# Save the best model with joblib
joblib.dump(best_model_object, '/content/best_model.joblib')
joblib.dump(best_model_object, '/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/best_model.joblib')

# Obtain the score of the best model
score = best_model_object.score(X, y)

# Print the score
print(f"Score of {best_model}: {score}")


ExtraTreesClassifier
Score of ExtraTreesClassifier: 0.7066326530612245


In [ ]:
blocos = []
used_names = set()
l = 'Label'
for i, row in data_labeled.head(100).iterrows():
    nome = row['file'].split('.')[0]
    if nome in used_names:
        continue
    used_names.add(nome)
    out = widgets.Output()
    with out:
        display(Image(f'/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/ConsultasDataset/Charts/{nome}.png'))
        display(f'Label: {"Inválido" if row[l] == 0 else "Válido"}')
        display(Audio(f'/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/ConsultasDataset/MP3/{nome}.mp3'))
        data_point = np.array(X_normalized[X_normalized.index == f'{nome}.mp3'].iloc[0].iloc[col_select])
        prediction = best_model_object.predict(data_point.reshape(1, -1))
        display(f'Model: {"Inválido" if prediction[0] == 0 else "Válido"}')
    blocos.append(out)
widgets.HBox(blocos)


# Test

In [ ]:
!unzip "/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/test.zip"

Archive:  /content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/test.zip
   creating: test/
   creating: test/valid/
 extracting: test/valid/a00659.mp3   
 extracting: test/valid/a01291.mp3   
   creating: test/invalid/
 extracting: test/invalid/a01332.mp3  
 extracting: test/valid/a01346.mp3   
 extracting: test/valid/a01315.mp3   
 extracting: test/valid/a01339.mp3   
 extracting: test/valid/a01316.mp3   
 extracting: test/invalid/a01304.mp3  
 extracting: test/invalid/a01302.mp3  
 extracting: test/invalid/a01331.mp3  
 extracting: test/invalid/a01334.mp3  
 extracting: test/invalid/a01322.mp3  


In [ ]:
from glob import glob
import librosa
from sklearn.metrics import classification_report

In [ ]:
testes = glob('/content/test/*/*.mp3')
validar = [(a, 1 if a.split('/')[3] == 'valid' else 0) for a in testes]
validar

[('/content/test/invalid/a01331.mp3', 0),
 ('/content/test/invalid/a01332.mp3', 0),
 ('/content/test/invalid/a01304.mp3', 0),
 ('/content/test/invalid/a01334.mp3', 0),
 ('/content/test/invalid/a01302.mp3', 0),
 ('/content/test/invalid/a01322.mp3', 0),
 ('/content/test/valid/a01315.mp3', 1),
 ('/content/test/valid/a01339.mp3', 1),
 ('/content/test/valid/a01346.mp3', 1),
 ('/content/test/valid/a01316.mp3', 1),
 ('/content/test/valid/a01291.mp3', 1),
 ('/content/test/valid/a00659.mp3', 1)]

In [ ]:
# Extração de recursos e aumento de dados
features = []
for file, label in tqdm(validar):
    y, sr = librosa.load(file)

    duration = librosa.get_duration(y=y, sr=sr)
    spectral_centroids = librosa.feature.spectral_centroid(y=y, sr=sr)
    spectral_contrast = librosa.feature.spectral_contrast(y=y, sr=sr)
    spectral_bandwidth = librosa.feature.spectral_bandwidth(y=y, sr=sr)
    spectral_rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr)
    zero_crossing_rate = librosa.feature.zero_crossing_rate(y)
    mfcc = librosa.feature.mfcc(y=y, sr=sr)
    rmse = librosa.feature.rms(y=y)
    chroma_stft = librosa.feature.chroma_stft(y=y, sr=sr)
    tonnetz = librosa.feature.tonnetz(y=y, sr=sr)
    melspectrogram = librosa.feature.melspectrogram(y=y, sr=sr)

    # Calculando np.mean, np.std e np.ptp
    features_dict = {}
    for feature, feature_name in zip([spectral_centroids, spectral_contrast, spectral_bandwidth, spectral_rolloff, zero_crossing_rate, mfcc, rmse, chroma_stft, tonnetz, melspectrogram],
                                      ['spectral_centroids', 'spectral_contrast', 'spectral_bandwidth', 'spectral_rolloff', 'zero_crossing_rate', 'mfcc', 'rmse', 'chroma_stft', 'tonnetz', 'melspectrogram']):
        mean = np.mean(feature, axis=1)
        std = np.std(feature, axis=1)
        ptp = np.ptp(feature, axis=1)

        # Descompactando os vetores em colunas separadas
        for i in range(len(mean)):
            features_dict[f'{feature_name}_mean_{i}'] = mean[i]
            features_dict[f'{feature_name}_std_{i}'] = std[i]
            features_dict[f'{feature_name}_ptp_{i}'] = ptp[i]

    # Adicionando nome do arquivo e duração
    features_dict['file'] = file.split('/')[4]
    features_dict['duration'] = duration
    features_dict['label'] = label

    features.append(features_dict) # Criar DataFrame


100%|██████████| 12/12 [00:08<00:00,  1.38it/s]


In [ ]:
# Creating a DataFrame
test_df = pd.DataFrame(features)

# Normalização
test_df_norm = test_df.copy()
test_df_norm[cols_to_normalize] = scaler.transform(test_df_norm[cols_to_normalize])

test_df_norm

spectral_centroids_mean_0  spectral_centroids_std_0  \
0                    0.274594                  0.265309   
1                    0.173102                  0.275645   
2                    0.232982                  0.220109   
3                    0.286794                  0.374824   
4                    0.028550                  0.208413   
5                    0.037489                  0.097919   
6                    0.496922                  0.408131   
7                    0.369621                  0.369305   
8                    0.182209                  0.200151   
9                    0.325301                  0.369772   
10                   0.277298                  0.420099   
11                   0.192246                  0.139958   

    spectral_centroids_ptp_0  spectral_contrast_mean_0  \
0                   0.712033                  0.843782   
1                   0.809822                  0.768150   
2                   0.748623                  0.822574   
3                   0.732786                  0.762763   
4                   0.766298                  0.930559   
5                   0.712327                  0.760081   
6                   0.689456                  0.806042   
7                   0.746087                  0.904376   
8                   0.747119                  0.969450   
9                   0.737233                  0.986776   
10                  0.761093                  0.866166   
11                  0.205333                  0.783597   

    spectral_contrast_std_0  spectral_contrast_ptp_0  \
0                  0.461397                 0.378608   
1                  0.484831                 0.449005   
2                  0.362235                 0.296738   
3                  0.582324                 0.308538   
4                  0.507998                 0.314183   
5                  0.251152                 0.154377   
6                  0.242872                 0.274116   
7                  0.391651                 0.401979   
8                  0.357231                 0.347494   
9                  0.555801                 0.430120   
10                 0.460606                 0.338155   
11                 0.338584                 0.227979   

    spectral_contrast_mean_1  spectral_contrast_std_1  \
0                   0.528841                 0.637549   
1                   0.780134                 1.010736   
2                   0.376351                 0.601616   
3                   0.799994                 1.150663   
4                   0.238018                 0.434016   
5                   0.095606                 0.261751   
6                   0.090076                 0.273702   
7                   0.130014                 0.238147   
8                   0.072748                 0.315265   
9                   0.128308                 0.356549   
10                  0.132066                 0.481037   
11                  0.109134                 0.290298   

    spectral_contrast_ptp_1  spectral_contrast_mean_2  ...  \
0                  0.743415                  0.703492  ...   
1                  0.687762                  0.737864  ...   
2                  0.519030                  0.499038  ...   
3                  0.495580                  0.757893  ...   
4                  0.369217                  0.209926  ...   
5                  0.320393                  0.071893  ...   
6                  0.256434                  0.078187  ...   
7                  0.647226                  0.278346  ...   
8                  0.517892                  0.058671  ...   
9                  0.080194                  0.093236  ...   
10                 0.334381                  0.177819  ...   
11                 0.377958                  0.141740  ...   

    melspectrogram_ptp_125  melspectrogram_mean_126  melspectrogram_std_126  \
0                 0.000243                 0.000440                0.000203   
1                 0.004005                 0.

In [ ]:
# Seleção de características
y = test_df_norm['label']
X_test_normalized = test_df_norm.drop(['file', 'label'], axis=1)
X_test = skb.transform(X_test_normalized)

In [ ]:
X_test.shape

(12, 50)

In [ ]:
y.shape

(12,)

In [ ]:
clf = joblib.load('/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/best_model.joblib')

y_pred = clf.predict(X_test)

print(classification_report(y, y_pred))

              precision    recall  f1-score   support

           0       0.83      0.83      0.83         6
           1       0.83      0.83      0.83         6

    accuracy                           0.83        12
   macro avg       0.83      0.83      0.83        12
weighted avg       0.83      0.83      0.83        12



In [ ]:
blocos = []
l = 'Label'
for file, label in validar:
    out = widgets.Output()
    with out:
        display(f'Label: {"Inválido" if label == 0 else "Válido"}')
        display(Audio(file))
        data_point = test_df_norm[test_df_norm['file'] == file.split('/')[4]]
        data_point = skb.transform(data_point.drop(['file', 'label'], axis=1))
        prediction = best_model_object.predict(data_point.reshape(1, -1))
        display(f'Model: {"Inválido" if prediction[0] == 0 else "Válido"}')
    blocos.append(out)
widgets.HBox(blocos)

## Separate dataset

In [ ]:
# prompt: Com o modelo funcionando corretamente, faça ele classificar todos os audios em /content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/ConsultasDataset/MP3 e criar uma nova pasta dataset com subpastas valid e invalid e colocar os arquivos lá dependendo da classificação

import os
import shutil

# Create the directory structure
os.makedirs("/content/dataset/valid", exist_ok=True)
os.makedirs("/content/dataset/invalid", exist_ok=True)

# Get a list of all audio files in the directory
audio_files = glob("/content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1/ConsultasDataset/MP3/*.mp3")

# Classify each audio file and move it to the appropriate directory
for audio_file in tqdm(audio_files):
    # Classify the audio file
    try:
      data = np.array(X_normalized[X_normalized.index == audio_file.split('/')[9]].iloc[0].iloc[col_select])

      prediction = best_model_object.predict(data.reshape(1, -1))

      # Move the audio file to the appropriate directory
      if prediction[0] == 0:
          shutil.copy(audio_file, "/content/dataset/invalid")
      else:
          shutil.copy(audio_file, "/content/dataset/valid")
    except:
      continue


In [217]:
!cp -r /content/dataset /content/drive/MyDrive/Colab Notebooks/ECOM09A/Atividade_1